In [355]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

filename = '../driver/alpaca.2hrRA15Dec-61a.csv'

In [356]:
    
# Helper function for plotly scatter plots
def plot_formating(title, xtitle, ytitle):
    title={
        'text': title,
        'font': {
            'size': 24,  # Increase the font size
            'color': 'black',  # Set the font color
            'family': 'Arial',  # Set the font family
        },
        'x': 0.5,  # Center the title
        'xanchor': 'center'
    }
    labels={
        "x": xtitle,
        "y": ytitle
    }
    bgcolor = 'rgba(200, 200, 250, 0.5)'
    return title,labels,xtitle,ytitle,bgcolor


In [357]:
# Define the conversion function
def convert_to_float(value):
    try:
        return float(value)
    except ValueError:
        return float('nan')
    
# Define the conversion function
def convert_to_arcsec(value):
    try: 
        value = float(value) % (360 * 3600)  # Normalize to 0-360 degrees in arc-seconds
        if value > 180 * 3600:
            value -= 360 * 3600  # Adjust to -180 to 180 degrees in arc-seconds
        elif value < -180 * 3600:
            value += 360 * 3600  # Adjust to -180 to 180 degrees in arc-seconds
        return value
    except ValueError:
        return float('nan')

# Define the conversion function
def convert_to_bool(value):
    try:
        return True if value=='True' else False
    except ValueError:
        return bool('nan')
    
converters_dict = {
    'Dataset': str,   
    'Time': convert_to_float,  
    'Tracking': convert_to_bool,    
    'Slewing': convert_to_bool,    
    'Gotoing': convert_to_bool,    
    'TargetRA': convert_to_float,  
    'TargetDEC': convert_to_float,  
    'AscomRA': convert_to_float,  
    'AscomDec': convert_to_float,  
    'AscomAlt': convert_to_float,  
    'AscomAz': convert_to_float,  
    'ErrorRA': convert_to_arcsec,  
    'ErrorDec': convert_to_arcsec,  
}

raw = pd.read_csv(filename,converters=converters_dict)
raw.columns = ['Log'] + raw.columns[1:].tolist()
raw['TimeStamp'] = raw.Log.str.extract(r'(\d{4}-\d{2}-\d{2}T\d{2}:\d{2}:\d{2}\.\d{3})') # Extract date and time using a regular expression
raw['TimeStamp'] = pd.to_datetime(raw.TimeStamp)                                        # Convert the extracted date and time to a timestamp
raw['TimeStampSec'] = (raw.TimeStamp - raw.TimeStamp[raw.Time==0].iloc[-1]).dt.total_seconds()
raw['Goto'] = raw.Log.str.extract(r'(GOTO ASCOM .*)')                                   # Extract GOTO ASCOM commands
raw['Sync'] = raw.Log.str.extract(r'(SYNC ASCOM .*)')                                   # Extract SYNC ASCOM commands
raw['TimeStamp'].fillna(method='ffill', inplace=True)
raw.set_index('TimeStamp',inplace=True)
bad = (~raw.Tracking) | (raw.Slewing) | (raw.Gotoing)
raw.ErrorRA[bad] = pd.NA
raw.ErrorDec[bad] = pd.NA
df=raw


C:\Users\Nina\AppData\Local\Temp\ipykernel_6852\319921343.py:50: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



C:\Users\Nina\AppData\Local\Temp\ipykernel_6852\319921343.py:50: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\Nina\AppData\Local\Temp\ipykernel_6852\319921343.py:53: FutureWarning:

ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in cert

In [358]:
df.loc[:, 'RA'] = df.ErrorRA
df.loc[:, 'Dec'] = df.ErrorDec
df.loc[:, 'RAFill'] = df.ErrorRA.fillna(method='ffill')
df.loc[:, 'DecFill'] = df.ErrorDec.fillna(method='ffill')
df.loc[:, 'TimeMin'] = (df.Time / 60).round(1)
df.loc[:, 'RAStdev15s'] = df.RA.rolling('15s',center=True).std()
df.loc[:, 'DecStdev15s'] = df.Dec.rolling('15s',center=True).std()
df.loc[:, 'RAStdev30s'] = df.RA.rolling('30s',center=True).std()
df.loc[:, 'DecStdev30s'] = df.Dec.rolling('30s',center=True).std()
df.loc[:, 'RAStdev60s'] = df.RA.rolling('60s',center=True).std()
df.loc[:, 'DecStdev60s'] = df.Dec.rolling('60s',center=True).std()

C:\Users\Nina\AppData\Local\Temp\ipykernel_6852\336020734.py:3: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

C:\Users\Nina\AppData\Local\Temp\ipykernel_6852\336020734.py:4: FutureWarning:

Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.



In [359]:
fig=go.Figure()
title,labels,xtitle,ytitle,bgcolor = plot_formating('Declination Error vs Time Elapsed','Time Elapsed (seconds)','Dec Error (arc seconds)')
fig.update_layout(title=title, xaxis_title=xtitle, yaxis_title=ytitle, plot_bgcolor=bgcolor)
# Add trace for Dec Error
fig.add_trace(go.Scatter(x=df.TimeStampSec, y=df.Dec, name='Dec Error', mode='markers'))
# Add trace for stdev
fig.add_trace(go.Scatter(x=df.TimeStampSec, y=df.DecStdev15s, name='15s Stdev', mode='markers'))
# Add points for all GOTOs
fig.add_trace(go.Scatter(
    x=df[df.Goto.notna()].TimeStampSec, y=df[df.Goto.notna()].DecFill,
    name='Goto', text=df[df.Goto.notna()].Goto, mode='markers', 
    marker=dict(size=10, color='red')
))
# Add points for all Syncs
fig.add_trace(go.Scatter(
    x=df[df.Sync.notna()].TimeStampSec, y=df[df.Sync.notna()].DecFill,
    name='Sync', text=df[df.Sync.notna()].Sync, mode='markers', 
    marker=dict(size=10, color='dark green')
))
fig.show()

In [360]:
fig=go.Figure()
title,labels,xtitle,ytitle,bgcolor = plot_formating('Right Ascension Error vs Time Elapsed','Time Elapsed (seconds)','RA Error (arc seconds)')
fig.update_layout(title=title, xaxis_title=xtitle, yaxis_title=ytitle, plot_bgcolor=bgcolor)
# Add trace for Dec Error
fig.add_trace(go.Scatter(x=df.TimeStampSec, y=df.RA, name='RA Error', mode='markers'))
# Add points for all GOTOs
fig.add_trace(go.Scatter(
    x=df[df.Goto.notna()].TimeStampSec, y=df[df.Goto.notna()].RAFill,
    name='Goto', text=df[df.Goto.notna()].Goto, mode='markers', 
    marker=dict(size=10, color='red')
))
# Add points for all Syncs
fig.add_trace(go.Scatter(
    x=df[df.Sync.notna()].TimeStampSec, y=df[df.Sync.notna()].RAFill,
    name='Sync', text=df[df.Sync.notna()].Sync, mode='markers', 
    marker=dict(size=10, color='dark green')
))
# Add trace for stdev
fig.add_trace(go.Scatter(x=df.TimeStampSec, y=df.RAStdev15s, name='15s Stdev', mode='markers'))
fig.show()

In [361]:
#fig.add_shape(
#     type="rect",
#     x0=540, x1=1000, y0=0, y1=1, yref='paper', 
#     fillcolor="lightgreen", opacity=0.3, layer="below", line_width=0
# )


In [362]:
m = d.melt(id_vars='TimeMin', value_vars=['RA', 'Dec'], var_name='Axis', value_name='Error')
title,labels,xtitle,ytitle,bgcolor = plot_formating('RA/Dec Error vs Time Elapsed','Time Elapsed (minutes)','Error (arc seconds)')
fig=px.scatter(x=m.TimeMin, y=m.Error, color=m.Axis, facet_col=m.Axis, labels=labels)
fig.update_layout(title=title, xaxis_title=xtitle, yaxis_title=ytitle, plot_bgcolor=bgcolor)
fig.show()